In [1]:
import numpy as np
from pathlib import Path

In [2]:
filelist = Path('../data/ns').glob('*.npy')

reynolds = []
data = []
for filepath in filelist:
    reynolds.append( int(filepath.stem.split('_')[-1]) )
    data.append( np.load(filepath) )

In [3]:
from utils import animate

sequence = data[0]
u = sequence[:,:,::3]
v = sequence[:,:,1::3]
p = sequence[:,:,2::3]
animate(u)

In [5]:
import torch
import torch.nn as nn

class Backbone(nn.Module):
    def __init__(self):
        super().__init__()

        self.fc1 = nn.Linear(3, 32)  # input dim = 3 (t, x, y)
        self.fc2 = nn.Linear(32, 16) # hidden dims = [32, 16]
        self.out = nn.Linear(16, 3)  # output dim = 3 (u, v, p)

    def forward(self, x):
        x = self.fc1(x)
        x = nn.ReLU()(x) 
        x = self.fc2(x)
        x = nn.ReLU()(x) 
        return self.out(x)

def navier_stokes_loss(model, X, Re):
    t = X[...,0].view(-1,1)
    x = X[...,1].view(-1,1)
    y = X[...,2].view(-1,1)
    out = model(X)
    u = out[...,0].view(-1,1)
    v = out[...,1].view(-1,1)
    p = out[...,2].view(-1,1)

    # derivatives
    u_x = torch.autograd.grad(u.sum(), x, create_graph=True)[0]
    u_y = torch.autograd.grad(u.sum(), y, create_graph=True)[0]
    u_t = torch.autograd.grad(u.sum(), t, create_graph=True)[0]
    v_x = torch.autograd.grad(v.sum(), x, create_graph=True)[0]
    v_y = torch.autograd.grad(v.sum(), y, create_graph=True)[0]
    v_t = torch.autograd.grad(v.sum(), t, create_graph=True)[0]
    p_x = torch.autograd.grad(p.sum(), x, create_graph=True)[0]
    p_y = torch.autograd.grad(p.sum(), y, create_graph=True)[0]
    
    u_xx = torch.autograd.grad(u_x.sum(), x, create_graph=True)[0]
    u_yy = torch.autograd.grad(u_y.sum(), y, create_graph=True)[0]
    v_xx = torch.autograd.grad(v_x.sum(), x, create_graph=True)[0]
    v_yy = torch.autograd.grad(v_y.sum(), y, create_graph=True)[0]

    
    f_equation_mass = u_x + v_y
    f_equation_x = u_t + (u * u_x + v * u_y) + p_x - 1.0 / Re * (u_xx + u_yy)
    f_equation_y = v_t + (u * v_x + v * v_y) + p_y - 1.0 / Re * (v_xx + v_yy)

    mse = torch.nn.MSELoss()
    batch_t_zeros = torch.zeros_like(x, dtype=torch.float32, device=self.device)
    mse_equation = mse(f_equation_x, batch_t_zeros) + mse(f_equation_y, batch_t_zeros) + \
                    mse(f_equation_mass, batch_t_zeros)


class PINN(nn.Module):
    def __init__(self, model, data_loss=None, physics_loss=None, device=torch.device("cuda:0" if torch.cuda.is_available() else "cpu")):
        super().__init__()
        
        self.device = device
        self.model = model
        
        if isinstance(data_loss, list):
            self.data_loss = data_loss
        else:
            self.data_loss = [data_loss]
        if isinstance(physics_loss, list):
            self.physics_loss = physics_loss
        else:
            self.physics_loss = [physics_loss]
        
        for name, param in self.model.named_parameters():
            if name.endswith('linear.weight'):
                nn.init.xavier_normal_(param)
            elif name.endswith('linear.bias'):
                nn.init.zeros_(param)

    def forward(self, x):
        return self.model(x)
    
    def loss(self, x, y):
        out = self.forward(x)

        loss = 0.
        for data_loss in self.data_loss:
            loss += data_loss(out, y)
        for physics_loss in self.physics_loss:
            loss += physics_loss(self.model, x)
    #     out = self.forward(t, x)
    #     u = out[:,0].reshape(-1,1)
    #     v = out[:,1].reshape(-1,1)
    #     p = out[:,2].reshape(-1,1)

    #     # derivatives
    #     u_x = torch.autograd.grad(u.sum(), x, create_graph=True)[0]
    #     u_y = torch.autograd.grad(u.sum(), y, create_graph=True)[0]
    #     u_t = torch.autograd.grad(u.sum(), t, create_graph=True)[0]
    #     v_x = torch.autograd.grad(v.sum(), x, create_graph=True)[0]
    #     v_y = torch.autograd.grad(v.sum(), y, create_graph=True)[0]
    #     v_t = torch.autograd.grad(v.sum(), t, create_graph=True)[0]
    #     p_x = torch.autograd.grad(p.sum(), x, create_graph=True)[0]
    #     p_y = torch.autograd.grad(p.sum(), y, create_graph=True)[0]
        
    #     u_xx = torch.autograd.grad(u_x.sum(), x, create_graph=True)[0]
    #     u_yy = torch.autograd.grad(u_y.sum(), y, create_graph=True)[0]
    #     v_xx = torch.autograd.grad(v_x.sum(), x, create_graph=True)[0]
    #     v_yy = torch.autograd.grad(v_y.sum(), y, create_graph=True)[0]

        
    #     f_equation_mass = u_x + v_y
    #     f_equation_x = u_t + (u * u_x + v * u_y) + p_x - 1.0 / Re * (u_xx + u_yy)
    #     f_equation_y = v_t + (u * v_x + v * v_y) + p_y - 1.0 / Re * (v_xx + v_yy)

    #     mse = torch.nn.MSELoss()
    #     batch_t_zeros = torch.zeros_like(x, dtype=torch.float32, device=self.device)
    #     mse_equation = mse(f_equation_x, batch_t_zeros) + mse(f_equation_y, batch_t_zeros) + \
    #                    mse(f_equation_mass, batch_t_zeros)
backbone = Backbone()
pinn = PINN(backbone)

In [98]:
H, W, T = sequence.shape
T = T//3

x = torch.arange(0, W)*1.
y = 0.5*H - torch.arange(0, H)
xx, yy = torch.meshgrid(x, y, indexing='xy')

predictions = []
for t in range(T):
    tt = t*torch.ones_like(xx)
    X = torch.stack([tt, xx, yy], 0)
    X = torch.flatten(X, start_dim=1).T
    pred = pinn(X)
    u = pred[...,0].view(H,W)
    v = pred[...,1].view(H,W)
    p = pred[...,2].view(H,W)
    predictions.append(u.detach().numpy())
    predictions.append(v.detach().numpy())
    predictions.append(p.detach().numpy())
predictions = np.transpose(predictions, [1,2,0])

In [63]:
u = predictions[:,:,::3]
v = predictions[:,:,1::3]
p = predictions[:,:,2::3]
animate(u)

In [88]:
for t in range(T):
    tt = t*torch.ones_like(xx)
    X = torch.stack([tt, xx, yy], 0)
    X = torch.flatten(X, start_dim=1).T
    Y = torch.tensor(sequence[:,:,3*t:3*t+3])
    Y = torch.flatten(Y, end_dim=1)
    if t == 0:
        x_train = X
        y_train = Y
    else:
        x_train = torch.cat([x_train,X], 0)
        y_train = torch.cat([y_train,Y], 0)

In [91]:
from torch.utils.data import TensorDataset, DataLoader
train_dataset = TensorDataset(x_train, y_train)
train_dataloader = DataLoader(train_dataset, batch_size=128, shuffle=True)

In [ ]:
N_EPOCHS = 1

optimizer = torch.optim.Adam(pinn.parameters(), lr=0.0001)

for epoch in range(N_EPOCHS):
    for x, y in train_dataloader:
        optimizer.zero_grad()
        pred = pinn(x)

        loss = 